In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from os import path, environ
import fiona
import numpy as N
import attitude
from attitude import Orientation, ReconstructedPlane, create_groups, disable_orientations
from attitude.display import plot_interactive
from json import dumps
from sys import argv

In [3]:
BASE = path.join(path.dirname(attitude.__file__),'..')
DATA = path.join(BASE,"ui-test/data")

In [78]:
fn = path.join(DATA,'elevations.dxf')

orientations = []
with fiona.open(fn) as ds:
    for i,item in ds.items():
        coords = N.array(item['geometry']['coordinates'])
        orientations.append(Orientation(coords))

In [79]:
groups = (
    ["ebab5ecb","afb1b38f","507f716f","beb6e9c3","10e2837e"],
    ["587a6ddd","491fc31a","f74c5469"],
    ["72417f52","ad1c05d7","eb31c4b0","495f76da","93d7af22"],
    ["c2122b2a","de785eb5"],
    ["587a6ddd","7b12f5d4"]
)

disabled = ["b4deb25a","99c9f7ae","72324fc0","ead57709","e550b0f5",
      "a830c0dd","ce55866c","2c0fa99d","a66556d9","9143d875","be28b5b1","16f85224","01bb2a47","60a10cff","bb51409a","df8e2dca",
       "9ab85b7c","a4813e83","a9aebbb7","22b36bca"]

groupedOrientations = create_groups(orientations, *groups,
                             same_plane=False)

groupedOrientations = [o for o in groupedOrientations if o.hash not in disabled]

collection = [a.to_mapping(color='#ff0000', type='remote')
              for a in groupedOrientations]

plot_interactive(collection)

ID: 
 Nominal plane 
 
 Strike: º 
 Dip: º 
 
 Angular errors 
 
 Min: 
 Max:

In [80]:
fn = path.join(DATA,'field-orientations.geojson')

with fiona.open(fn) as ds:
    for i,item in ds.items():
        p = item['properties']
        if p['planeType'].strip() != 'Bedding':
            continue

        asm = p.get("aster_smoothed")
        alt = asm

        alt -= 30 # Global datum is higher than local
        center = (*item['geometry']['coordinates'],alt)

        a = ReconstructedPlane(p['strike'], p['dip'],0,0.001,0.001)
        orientation = a.to_mapping(
            center=center,
            color='#444', type='in-situ')
        collection.append(orientation)

In [81]:
plot_interactive(collection)

ID: 
 Nominal plane 
 
 Strike: º 
 Dip: º 
 
 Angular errors 
 
 Min: 
 Max: